In [1]:
import os
import sys
module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
os.chdir(module_path)

In [35]:
from utils.mano import ManoLayer
from utils import utils
import plotly.graph_objects as go

mano_layer = ManoLayer()
anno = utils.load_ho_meta("/home/shugo/workspace/rendering/data/HO3D_v3/train/MDF11/meta/1016.pkl")
mano = mano_layer(anno)

obj_verts, obj_faces, obj_uv, obj_map = utils.get_obj_mesh(anno)
obj_verts = utils.apply_transform_to_mesh(obj_verts, anno)

fig = go.Figure()
utils.add_mesh_to_fig(fig, mano.vertices[0], mano_layer.faces, opacity=0.2)
utils.add_mesh_to_fig(fig, obj_verts, obj_faces, opacity=0.2)
fig.add_trace(
    go.Scatter3d(
        x=mano.joints[0][:, 0],
        y=mano.joints[0][:, 1],
        z=mano.joints[0][:, 2],
        mode='markers',
        marker=dict(
            size=2,
            color='red',
            opacity=0.5,
        ),
        text=[f'joint {i}' for i in range(mano.joints.shape[1])],
        # hoverinfo='text',
        textposition='top center',
        name='mano.joints',
    )
)
fig.add_trace(
    go.Scatter3d(
        x=anno['handJoints3D'][:, 0],
        y=anno['handJoints3D'][:, 1],
        z=anno['handJoints3D'][:, 2],
        mode='markers',
        marker=dict(
            size=1,
            color='blue',
        ),
        name='handJoints3D',
    )
)

for i in range(16):
    if mano_layer.parents[i] == -1:
        continue
    fig.add_trace(
        go.Scatter3d(
            x=[mano.joints[0][i, 0], mano.joints[0][mano_layer.parents[i], 0]],
            y=[mano.joints[0][i, 1], mano.joints[0][mano_layer.parents[i], 1]],
            z=[mano.joints[0][i, 2], mano.joints[0][mano_layer.parents[i], 2]],
            mode='lines',
            name=f'bone{i}->{mano_layer.parents[i]}',
        )
    )
fig.show()

/home/shugo/workspace/rendering/utils/utils.py:18: FutureWarning:

elementwise comparison failed; returning scalar instead, but in the future will perform elementwise comparison



torch.Size([9174, 3]) torch.Size([3, 3]) torch.Size([3])


In [3]:
print(mano.joints.shape)
print(mano_layer.mano_layer['right'].__dict__.keys())
print(mano_layer.mano_layer['right'].parents)
# dir(mano_layer.mano_layer['right'])

torch.Size([1, 16, 3])
dict_keys(['num_pca_comps', 'is_rhand', 'gender', 'age', 'training', '_parameters', '_buffers', '_non_persistent_buffers_set', '_backward_hooks', '_is_full_backward_hook', '_forward_hooks', '_forward_pre_hooks', '_state_dict_hooks', '_load_state_dict_pre_hooks', '_load_state_dict_post_hooks', '_modules', 'batch_size', '_num_betas', 'dtype', 'joint_mapper', 'faces', 'use_pca', 'flat_hand_mean', 'np_hand_components'])
tensor([-1,  0,  1,  2,  0,  4,  5,  0,  7,  8,  0, 10, 11,  0, 13, 14])


In [4]:
anno.keys()

dict_keys(['handBeta', 'handTrans', 'handPose', 'handJoints3D', 'camMat', 'objRot', 'objTrans', 'camIDList', 'objCorners3D', 'objCorners3DRest', 'objName', 'objLabel', 'handVertContact', 'handVertDist', 'handVertIntersec', 'handVertObjSurfProj'])

In [5]:
# anno['handPose'].shape
print(anno['handJoints3D'])

[[-0.07221958  0.03996737 -0.40746005]
 [ 0.01549277  0.02175211 -0.4358996 ]
 [ 0.05016312  0.01478204 -0.43879767]
 [ 0.07131393  0.00414449 -0.44353217]
 [ 0.02037698  0.00752373 -0.41572092]
 [ 0.05091133 -0.00545394 -0.4178655 ]
 [ 0.07057891 -0.02009792 -0.42340609]
 [-0.01209467 -0.01643601 -0.38755039]
 [ 0.00439771 -0.03256481 -0.38989394]
 [ 0.01834203 -0.04734168 -0.39510839]
 [ 0.00404265 -0.00512995 -0.39769447]
 [ 0.02895248 -0.02295148 -0.40268356]
 [ 0.04636442 -0.04312239 -0.4091771 ]
 [-0.0510548   0.03596358 -0.44032781]
 [-0.03792543  0.02282704 -0.46801226]
 [-0.02753769  0.00399472 -0.48785504]
 [-0.01143981 -0.01649537 -0.51619728]
 [ 0.09062004 -0.01391113 -0.45239375]
 [ 0.08756573 -0.04139663 -0.43253164]
 [ 0.06240512 -0.06553325 -0.41750212]
 [ 0.03243981 -0.0627774  -0.40380143]]


# Load ManipNet output

In [38]:
import numpy as np

output_np = np.loadtxt("/home/shugo/workspace/rendering/data/output/manipnet_pred.txt")
output_np.shape
output_pos = output_np[:3*22].reshape(-1, 3)
output_rot = output_np[3*22:192].reshape(-1, 6)
output_dist = output_np[192:]
print(output_pos.shape, output_rot.shape, output_dist.shape)

output_pos += mano.joints[0][0:1].numpy()
mano_index = [0, 
                1,2,3,#4
                5,6,7,#8
                9,10,11,#12
                13,14,15,#16 17
                18,19,20,#21
            ]
print(len(mano_index))
output_pos_mano16 = output_pos[mano_index]
manipnet_parent = [-1, 
                   0, 1, 2, 3,
                   0, 5, 6, 7, 
                   0, 9, 10, 11, 
                   0, 13, 14, 15, 
                   0, 17, 18, 19, 20 
                ]


(22, 3) (21, 6) (22,)
16


In [39]:
fig = go.Figure()
utils.add_mesh_to_fig(fig, mano.vertices[0], mano_layer.faces, opacity=0.2)
utils.add_mesh_to_fig(fig, obj_verts, obj_faces, opacity=0.2)
fig.add_trace(
    go.Scatter3d(
        x=mano.joints[0][:, 0],
        y=mano.joints[0][:, 1],
        z=mano.joints[0][:, 2],
        mode='markers',
        marker=dict(
            size=2,
            color='red',
            opacity=0.5,
        ),
        text=[f'joint {i}' for i in range(mano.joints.shape[1])],
        # hoverinfo='text',
        textposition='top center',
        name='mano.joints',
    )
)
fig.add_trace(
    go.Scatter3d(
        x=anno['handJoints3D'][:, 0],
        y=anno['handJoints3D'][:, 1],
        z=anno['handJoints3D'][:, 2],
        mode='markers',
        marker=dict(
            size=1,
            color='blue',
        ),
        name='handJoints3D',
    )
)
fig.add_trace(
    go.Scatter3d(
        x=output_pos[:, 0],
        y=output_pos[:, 1],
        z=output_pos[:, 2],
        mode='markers',
        marker=dict(
            size=1,
            color='green',
        ),
        name='output_pos',
    )
)

for i in range(16):
    if mano_layer.parents[i] == -1:
        continue
    fig.add_trace(
        go.Scatter3d(
            x=[mano.joints[0][i, 0], mano.joints[0][mano_layer.parents[i], 0]],
            y=[mano.joints[0][i, 1], mano.joints[0][mano_layer.parents[i], 1]],
            z=[mano.joints[0][i, 2], mano.joints[0][mano_layer.parents[i], 2]],
            mode='lines',
            name=f'bone{i}->{mano_layer.parents[i]}',
        )
    )

for i in range(21):
    if manipnet_parent[i] == -1:
        continue
    fig.add_trace(
        go.Scatter3d(
            # x=[output_pos_mano16[i, 0], output_pos_mano16[mano_layer.parents[i], 0]],
            # y=[output_pos_mano16[i, 1], output_pos_mano16[mano_layer.parents[i], 1]],
            # z=[output_pos_mano16[i, 2], output_pos_mano16[mano_layer.parents[i], 2]],
            x=[output_pos[i, 0], output_pos[manipnet_parent[i], 0]],
            y=[output_pos[i, 1], output_pos[manipnet_parent[i], 1]],
            z=[output_pos[i, 2], output_pos[manipnet_parent[i], 2]],
            mode='lines',
        )
    )

fig.show()